# Installing necessary libraries

In [ ]:
!pip install transformers datasets evaluate
!pip install transformers[torch]
!pip install accelerate -U

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.2/7.2 MB 51.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 486.2/486.2 kB 41.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.4/81.4 kB 7.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 236.8/236.8 kB 23.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 84.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 79.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 14.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.5/212.5 kB 27.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.3/134.3 kB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 46.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.5/114.5 kB 14.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━

# Importing Libraries

In [ ]:
import pandas as pd
from huggingface_hub import notebook_login
from datasets import load_dataset
from transformers import AutoTokenizer
from transformers import DefaultDataCollator
from transformers import AutoModelForQuestionAnswering, TrainingArguments, Trainer
from transformers import pipeline

# Log in to Huggingface

In [ ]:
notebook_login()

# Downloading 5000 context question-answer pairs from squad

In [ ]:
squad = load_dataset("squad", split="train[:5000]")

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating train split:   0%|          | 0/87599 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/10570 [00:00<?, ? examples/s]

Dataset squad downloaded and prepared to /root/.cache/huggingface/datasets/squad/plain_text/1.0.0/d6ec3ceb99ca480ce37cdd35555d6cb2511d223b9150cce08a837ef62ffea453. Subsequent calls will reuse this data.


In [ ]:
squad = squad.train_test_split(test_size=0.2) #splitting the data into test and train in 80% to 20% ratio

In [ ]:
print("Size of Training data : ",len(squad["train"]))
print("Size of Testing Data :", len(squad["test"]))

Size of Training data :  4000
Size of Testing Data : 1000


# Example of training data

In [ ]:
df=pd.DataFrame()

for i in range(5):
  title=squad["train"][i]['title']
  context=squad["train"][i]['context']
  ques=squad["train"][i]['question']
  ans=squad["train"][i]['answers']
  QA_input = {
    'question': ques,
    'context':  title+context}
  df=pd.concat([df,pd.DataFrame({'title':title,'context':context,'ques':ques,'ans':ans['text']})])

df.head()

title  \
0                   Beyoncé   
0               Antibiotics   
0  University_of_Notre_Dame   
0                   Beyoncé   
0             New_York_City   

                                             context  \
0  On February 6, 2016, one day before her perfor...   
0  The majority of studies indicate antibiotics d...   
0  As at most other universities, Notre Dame's st...   
0  In December, Beyoncé along with a variety of o...   
0  New York City is home to the headquarters of t...   

                                                ques  \
0       What kind of platform was the song released?   
0  What percentage of birth control pill failure ...   
0  In what year did the student paper Common Sens...   
0  What school shooting prompted the creation of ...   
0  How many professional sports leagues have thei...   

                            ans  
0               music streaming  
0                      about 1%  
0                          1987  
0  Sandy Hook Elementary School  
0                          five

# Fine Tuning DistilBert

## Loading tokenizer

In [ ]:
tokenizer = AutoTokenizer.from_pretrained("distilbert-base-uncased")

In [ ]:
def preprocess_function(examples):
    print(examples,type(examples))
    questions = [q.strip() for q in examples["question"]]
    inputs = tokenizer(
        questions,
        examples["context"],
        max_length=384,
        truncation="only_second",
        return_offsets_mapping=True,
        padding="max_length",
    )

    offset_mapping = inputs.pop("offset_mapping")
    answers = examples["answers"]
    start_positions = []
    end_positions = []

    for i, offset in enumerate(offset_mapping):
        answer = answers[i]
        start_char = answer["answer_start"][0]
        end_char = answer["answer_start"][0] + len(answer["text"][0])
        sequence_ids = inputs.sequence_ids(i)

        # Find the start and end of the context
        idx = 0
        while sequence_ids[idx] != 1:
            idx += 1
        context_start = idx
        while sequence_ids[idx] == 1:
            idx += 1
        context_end = idx - 1

        # If the answer is not fully inside the context, label it (0, 0)
        if offset[context_start][0] > end_char or offset[context_end][1] < start_char:
            start_positions.append(0)
            end_positions.append(0)
        else:
            # Otherwise it's the start and end token positions
            idx = context_start
            while idx <= context_end and offset[idx][0] <= start_char:
                idx += 1
            start_positions.append(idx - 1)

            idx = context_end
            while idx >= context_start and offset[idx][1] >= end_char:
                idx -= 1
            end_positions.append(idx + 1)

    inputs["start_positions"] = start_positions
    inputs["end_positions"] = end_positions
    return inputs

In [ ]:
tokenized_squad = squad.map(preprocess_function, batched=True, remove_columns=squad["train"].column_names)  #Applying preprocessing to the entire dataset

data_collator = DefaultDataCollator()

Map:   0%|          | 0/4000 [00:00<?, ? examples/s]

{'id': ['56bfa8bba10cfb140055120f', '57302106a23a5019007fcdf8', '5733bf84d058e614000b61c1', '56d4fa2e2ccc5a1400d833cb', '56d10dd217492d1400aab83a', '5731c593e17f3d14004223c5', '56cfb240234ae51400d9be96', '56cffde2234ae51400d9c22b', '56bfae97a10cfb1400551235', '56ce6629aab44d1400b8874d', '56cfe88d234ae51400d9c075', '56d53a0e2593cc1400307af7', '56d13443e7d4791d00901feb', '56d5d41b1c85041400946e0f', '56cecdf0aab44d1400b88a93', '56cf3569aab44d1400b88e55', '56d4c2b22ccc5a1400d831f4', '57301a6b04bcaa1900d7719f', '56d4e91b2ccc5a1400d83334', '56cf5adaaab44d1400b890f1', '56d521ee2593cc1400307aa1', '56d4e2e12ccc5a1400d832f0', '5732843bb3a91d1900202df7', '5733b4cf4776f419006610ca', '5733963c4776f41900660df8', '56d1085d17492d1400aab7a9', '56d120c117492d1400aaba11', '56cfad77234ae51400d9be60', '56cfafaf234ae51400d9be68', '56d4f9112ccc5a1400d833ba', '56bfd351a10cfb1400551311', '56bf6e823aeaaa14008c962a', '56d120c117492d1400aaba0d', '57321200e17f3d140042265f', '56cffcb0234ae51400d9c208', '56d31bfb59d

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

{'id': ['56cf331faab44d1400b88e1f', '56cf582eaab44d1400b8909e', '56d1191d17492d1400aab933', '56d313b559d6e41400146211', '56d38cc659d6e4140014672d', '56cc803f6d243a140015efbc', '56cf70c74df3c31400b0d79c', '56cee70daab44d1400b88c55', '5734215f4776f419006618fc', '56cef8faaab44d1400b88d68', '56cfb1a2234ae51400d9be86', '56d1324717492d1400aabbfb', '56d3a9282ccc5a1400d82dc8', '56cebb71aab44d1400b88954', '56cedf11aab44d1400b88b95', '56d1900ee7d4791d00902065', '56cd8ffa62d2951400fa6720', '56cef532aab44d1400b88d19', '56d38ac959d6e414001466cf', '56cbfbdd6d243a140015ee39', '56d00d6d234ae51400d9c2e4', '56cc41416d243a140015eee6', '56cfe43c234ae51400d9c010', '56d1d3fee7d4791d00902266', '5733f18ad058e614000b6643', '56cdd4d762d2951400fa68cf', '56d4f6e02ccc5a1400d833a1', '56d4f9902ccc5a1400d833c2', '56d65a4b1c850414009470b2', '56d4e0e92ccc5a1400d832db', '56d1053c17492d1400aab74c', '56bea27b3aeaaa14008c9199', '56cf38a9aab44d1400b88e9a', '56cf37b9aab44d1400b88e84', '573425624776f4190066195a', '56cffbdd234

## Loading distilbert model



In [ ]:
model = AutoModelForQuestionAnswering.from_pretrained("distilbert-base-uncased")

Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForQuestionAnswering: ['vocab_projector.bias', 'vocab_layer_norm.bias', 'vocab_layer_norm.weight', 'vocab_transform.bias', 'vocab_transform.weight']
- This IS expected if you are initializing DistilBertForQuestionAnswering from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForQuestionAnswering from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForQuestionAnswering were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['qa_outputs.bias', 'qa_outputs.weight']
You should probably TRAIN this model on a down-stream task to

## Training

In [ ]:
training_args = TrainingArguments(
    output_dir="QA_model-distilbert",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=3,
    weight_decay=0.01,
    push_to_hub=True,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_squad["train"],
    eval_dataset=tokenized_squad["test"],
    tokenizer=tokenizer,
    data_collator=data_collator,
)

trainer.train()

## Saving the model to huggingface




In [ ]:
trainer.push_to_hub()

# Fine Tuning Roberta

## Loading tokenizer


In [ ]:
tokenizer = AutoTokenizer.from_pretrained("deepset/roberta-base-squad2")

## Loading roberta model


In [ ]:
model = AutoModelForQuestionAnswering.from_pretrained("deepset/roberta-base-squad2")

## Training

In [ ]:
training_args = TrainingArguments(
    output_dir="QA_model-valhalla",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=3,
    weight_decay=0.01,
    push_to_hub=True,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_squad["train"],
    eval_dataset=tokenized_squad["test"],
    tokenizer=tokenizer,
    data_collator=data_collator,
)

trainer.train()

## Saving the model to huggingface

In [ ]:
trainer.push_to_hub()


# Evaluating the model

In [ ]:
question = "How many programming languages does BLOOM support?"
context = "BLOOM has 176 billion parameters and can generate text in 46 languages natural languages and 13 programming languages."

question_answerer = pipeline("question-answering", model="SMD00/QA_model-distilbert")
question_answerer(question=question, context=context)

{'score': 0.24583932757377625,
 'start': 58,
 'end': 95,
 'answer': '46 languages natural languages and 13'}

In [ ]:
question = "How many programming languages does BLOOM support?"
context = "BLOOM has 176 billion parameters and can generate text in 46 languages natural languages and 13 programming languages."

question_answerer = pipeline("question-answering", model="SMD00/QA_model-roberta")
question_answerer(question=question, context=context)

{'score': 0.9936482310295105, 'start': 93, 'end': 95, 'answer': '13'}